In [1]:
## TESTS START FROM LINE 2156 (tomohara-aliases.bash)

## Bracketed Paste is disabled to prevent characters after output
## Example: 
# $ echo 'Hi'
# | Hi?2004l

bind 'set enable-bracketed-paste off'

In [2]:
## TEST:  Make sure simple prompt used (e.g., no escapes that might contaminate output)
## PS1="$ "
## TODO: PS1="> "

## NOTE: The Jupyter bash kernel requires that PS1 not be modified as they customize it. 
echo $PS1

[PEXP\[\]ECT_PROMPT>


In [3]:
# Delete all aliases and function
# TODO: Instead start from pristine environment
unalias -a
alias | wc -l
for f in $(typeset -f | egrep '^\w+'); do unset -f $f; done
typeset -f | egrep '^\w+' | wc -l

0
0


In [4]:
# Setting a temp directory for tests
TMP=/tmp/test-py-commands

## NOTE: Source it directly from the ./tests directory.
BIN_DIR=$PWD/..

## TAKES EXTREMELY LONG TIME TO SOURCE THE MAIN BASH FILEII
# source tomohara-aliases.bash

alias | wc -l

0


In [5]:
## NOTE: For reproducability, the directory name needs to be fixed
## In place of $$, use a psuedo random number (e,g., 3443)
## *** All output from one run to the next needs to be the same ***

## temp_dir=$TMP/test-$$
temp_dir=$TMP/test-3443

mkdir -p "$temp_dir"
# TODO: /bin/rm -rvf "$temp_dir"
cd "$temp_dir"
pwd

#ALIAS FOR PRINTING SEPERATION LINES (FOR JUPYTER)
alias linebr="printf '%*s\n' "${COLUMNS:-$(tput cols)}" '' | tr ' ' -"

/tmp/test-py-commands/test-3443


In [6]:
# Count aliases proper
alias | wc -l
# Count functions
typeset -f | egrep '^\w+' | wc -l

1
0


In [7]:
export PYTHON_CMD="/usr/bin/time python -u"
export PYTHON="$NICE $PYTHON_CMD"
export PYTHONPATH="$HOME/python:$PYTHONPATH"

In [8]:
# add-python-path(pkg-dir): add PKG-DIR to PATH and PARENT to PYTHONPATH
## HACK: make sure Mezcla/mezcla resolves before python/mezcla
## OLD: export PYTHONPATH="$HOME/python/Mezcla:$PYTHONPATH"
function add-python-path () {
    local package_path="$1"
    local parent_path=$(realpath "$package_path/..")
    # add package to path (e.g., $HOME/python/Mezcla/mezcla)
    prepend-path "$package_path"
    # add parent to python-path spec (e.g., $HOME/python/Mezcla)
    export PYTHONPATH="$parent_path:$PYTHONPATH"
}
# EX: mezcla-devel; which system.py | grep -i Mezcla-main => ""
# note: mezcla-devel should be stable version of mezcla-tom
## OLD: alias mezcla-devel='add-python-path $HOME/programs/python/mezcla-tom/mezcla'
alias mezcla-devel='add-python-path $HOME/python/Mezcla/mezcla'
alias mezcla-main='add-python-path $HOME/python/Mezcla-main/mezcla'
alias mezcla-tom='add-python-path $HOME/python/Mezcla-tom/mezcla'
# Add mezcla-devel unless another version in path
if [[ ! "$PATH" =~ mezcla ]]; then
    ## OLD: mezcla-devel
    ## TODO: echo "Warning: mezcla not in PATH"
    true
fi

In [9]:
## FUNCTIONS REQUIRED FOR SMOOTH RUNNING OF THE TESTS
function ps-all () { 
    local pattern="$1";
    local pager=cat;
    if [ "$pattern" = "" ]; then 
        pattern="."; 
        pager=$PAGER
    fi;
    ps_mine.sh --all | $EGREP -i "((^USER)|($pattern))" | $pager;
    }
# Path settings
# TODO: define a function for removing duplicates from the PATH while
# preserving the order
function show-path-dir () { (echo "${1}:"; printenv "$1" | perl -pe "s/:/\n/g;") | $PAGER; }
alias show-path='show-path-dir PATH'
# append-path(path): appends PATH to environment variable unless already there
## TODO: function in-path { local path=$(tr ":" "\n" | $GREP "^$1$$"); return ($path != ""); }
# TODO: add force argument to ensure last (or first)
function append-path () { if [[ ! (($PATH =~ ^$1:) || ($PATH =~ :$1:) || ($PATH =~ :$1$)) ]]; then export PATH="${PATH}:$1"; fi }
function prepend-path () { if [[ ! (($PATH =~ ^$1:) || ($PATH =~ :$1:) || ($PATH =~ :$1$)) ]]; then export PATH="$1:${PATH}"; fi }
# TODO: rework append-/prepend-path and python variants via generic helper
function append-python-path () { export PYTHONPATH=${PYTHONPATH}:"$1"; }
function prepend-python-path () { export PYTHONPATH="$1":${PYTHONPATH}; }
 

In [10]:
# add-python-path $temp_dir
add-python-path $temp_dir

In [11]:
alias ps-python-full='ps-all python'
# note: excludes ipython and known system-related python scripts
alias ps-python='ps-python-full | $EGREP -iv "(screenlet|ipython|egrep|update-manager|software-properties|networkd-dispatcher)"'
alias show-python-path='show-path-dir PYTHONPATH'

In [12]:
## ERROR 1 - process ID list syntax error

# $ ps-python-full
# | error: process ID list syntax error
# | 
# | Usage:
# |  ps [options]
# | 
# |  Try 'ps --help <simple|list|output|threads|misc|all>'
# |   or 'ps --help <s|l|o|t|m|a>'
# |  for additional help text.
# | 
# | For more details see ps(1).

In [13]:
## ERROR 2 - bash : command not found and process ID list syntax error
# $ ps-python
# | bash: -iv: command not found
# | error: process ID list syntax error
# | 
# | Usage:
# |  ps [options]
# | 
# |  Try 'ps --help <simple|list|output|threads|misc|all>'
# |   or 'ps --help <s|l|o|t|m|a>'
# |  for additional help text.
# | 
# | For more details see ps(1).


In [14]:
## show-python-path DISPLAYS ALL THE AVAILABLE PATHS OF PYTHON
show-python-path

PYTHONPATH:
/tmp/test-py-commands
/home/aveey/python



In [15]:
# Python-lint filtering
# python-lint-full(filename): complete output from pylint, with caret-based
# context indicators retained by substiting carriage return for newline.
# python-lint-work(filename): pylint with moderate filtering
# python-lint(filename): pylint with usual filtering
# TODO: specify exclusion types in pylint command line (e.g., invalid-name)
# example: "C:674, 0: Invalid constant name "term_freq" (invalid-name)"
# example: "run_ner.py:413:0: C0330: Wrong continued indentation (add 8 spaces).
#                   'B-DATE', 'I-DATE', 'B-DOCTOR', 'I-DOCTOR', 'B-LOCATION', 'I-LOCATION', 'B-AGE', 'I-AGE',
#                   ^       | (bad-continuation)
# TODO: make Mercurial root-to-python-path hack optional
# TODO: add similar aliases for pep8 and pyflakes
# TODO: handle continutations of statements without indentation:
#   ner_eval/ner_detokenize.py:11:45: C0326: Exactly one space required after comma
#   parser.add_argument('--output_file', type=str,  help='')
#                                      ^ (bad-whitespace)

function python-lint-full() { 
    local root=$(hg root 2> /dev/null);
    ## TODO: --persistent=n (to avoid caching)
    PYTHONPATH="$root:.:$PYTHONPATH" $NICE pylint "$@" | perl -00 -ne 'while (/(\n\S+:\s*\d+[^\n]+)\n( +)/) { s/(\n\S+:\s*\d+[^\n]+)\n( +)/$1\r$2/mg; } print("$_");' 2>&1 | $PAGER;
}

In [16]:

# python-lint-full (scores the code on the basis of effectiveness)
python-lint-full $BIN_DIR/tests/batspp.py


Fatal Python error: init_sys_streams: can't initialize sys standard streams
Python runtime state: core initialized
Traceback (most recent call last):
  File "/usr/lib/python3.10/io.py", line 52, in <module>
  File "/tmp/test-py-commands/test-3443/abc.py", line 1, in <module>
RuntimeError: lost sys.stdout


In [17]:
# Notes:
# - filters out context in addition to warning proper, as in following:
#    ex: C:244, 0: Exactly one space required after assignment
#    SKIP_ADS =  (IS_GI_JOB_SEARCH or system.getenv_bool("SKIP_ADS", False))
#             ^ (bad-whitespace)
# - filters out other extraneous output
#   ex: Your code has been rated at 7.43/10 ...
#   ex: No config file found ...
# - the following has two regex: *modify the first* to add more conditions to ignore; the second is just for the extraneous pylint output
function python-lint-work() { python-lint-full "$@" 2>&1 | $EGREP -v '\((bad-continuation|bad-option-value|fixme|invalid-name|locally-disabled|too-few-public-methods|too-many-\S+|trailing-whitespace|star-args|unnecessary-pass)\)' | $EGREP -v '^(([A-Z]:[0-9]+)|(Your code has been rated)|(No config file found)|(\-\-\-\-\-))' | $PAGER; }
# TODO: rename as python-lint-tpo for clarity (and make python-lint as alias for it)
function python-lint() { python-lint-work "$@" 2>&1 | $EGREP -v '(Exactly one space required)|\((bad-continuation|bad-whitespace|bad-indentation|bare-except|c-extension-no-member|consider-using-enumerate|consider-using-with|global-statement|global-variable-not-assigned|keyword-arg-before-vararg|len-as-condition|line-too-long|logging-not-lazy|misplaced-comparison-constant|missing-final-newline|redefined-variable-type|redundant-keyword-arg|superfluous-parens|too-many-arguments|too-many-instance-attributes|trailing-newlines|useless-\S+|wrong-import-order|wrong-import-position)\)' | $PAGER; }


In [18]:
## ERROR GENERATED : -v COMMAND NOT FOUND
# $ python-lint-work $BIN_DIR/tests/batspp.py
# | bash: -v: command not found

In [19]:
## ERROR GENERATED : -v COMMAND NOT FOUND
# $ python-lint $BIN_DIR/tests/batspp.py
# | bash: -v: command not found

In [20]:
# run-python-lint-batched([file_spec="*.py"]: Run python-lint in batch mode over
# files in FILE_SPEC, placing results in pylint/<today>.
#
function get-python-lint-dir () {
    local python_version_major=$(pylint --version 2>&1 | extract_matches.perl "Python (\d)")
    local affix="py${python_version_major}"
    local out_dir="_pylint/$(todays-date)-$affix"
    echo "$out_dir"
}
#
function run-python-lint-batched () {
    # TODO: support files with embedded spaces
    local file_spec="$@"
    if [ "$file_spec" = "" ]; then file_spec="*.py"; fi

    # Create output directory if needed
    local out_dir=$(get-python-lint-dir)
    mkdir -p "$out_dir"

    # Run pylint and pipe top section into less
    (for f in $($LS $file_spec); do
         # HACK: uses basename of parent prefix if invoked with path
         local b=$(basename "$f")
         local pre=""
	 # Note: uses directory name as prefix if file not in current dir
         if [[ $f =~ / ]]; then pre="$(basename $(dirname "$f"))-"; fi
         DEBUG_LEVEL=5 python-lint "$f" >| "$out_dir/$pre$b".log 2>&1
         head "$out_dir/$pre$b".log
     done) >| "$out_dir/summary.log"
    less -p '^\** Module' "$out_dir/summary.log";
}

In [21]:
# (REQUIRED BY run-python-lint-batched)

function downcase-stdin { perl -pe "use open ':std', ':encoding(UTF-8)'; s/.*/\L$&/;"; }
function downcase-text() { echo "$@" | downcase-stdin; }
# todays-date(): outputs date in format DDmmmYY (e.g., 22Apr20)
## OLD: function todays-date() { date '+%d%b%y' | perl -pe 's/.*/\L$&/;'; }
## TODO: drop leading digits in day of month
## NOTE: keep in synch with common.perl get_file_ddmmmyy and .emacs edit-adhoc-notes-file
function todays-date() { date '+%d%b%y' | downcase-stdin; }


In [22]:
# ERROR: Pattern not found  (press RETURN)
# run-python-lint-batched ./print.py 

In [23]:
# python-import-path(module): find path for package directory of MODULE
# Note: this checks output via module initialization output shown with python -v
# ex: /usr/local/misc/programs/anaconda3/lib/python3.8/site-packages/sklearn/__pycache__/__init__.cpython-38.pyc matches /usr/local/misc/programs/anaconda3/lib/python3.8/site-packages/sklearn/__init__.py

function python-import-path-all() { local module="$1"; python -u -v -c "import $module" 2>&1; }
function python-import-path-full() { local module="$1"; python-import-path-all "$@" | extract_matches.perl "((matches (.*\W$module[^/]*[/\.][^/]*))|ModuleNotFoundError)"; }
function python-import-path() { python-import-path-full "$@" | head -1; }


In [24]:
# RETURNS A LIST OF PYTHON MODULES
rm -rf ./*
pip3 freeze

asttokens==2.0.5
Babel==2.10.1
backcall==0.2.0
bash_kernel @ git+https://github.com/kdm9/bash_kernel.git@a4c81c9f35926b7625b11e4c016c5e67edac522f
batspp @ file:///home/aveey/tom-project/shell-scripts/batspp
brotlipy==0.7.0
certifi==2021.10.8
cffi @ file:///opt/conda/conda-bld/cffi_1642701102775/work
charset-normalizer @ file:///tmp/build/80754af9/charset-normalizer_1630003229654/work
click==8.1.3
colorama @ file:///tmp/build/80754af9/colorama_1607707115595/work
conda==4.12.0
conda-content-trust @ file:///tmp/build/80754af9/conda-content-trust_1617045594566/work
conda-package-handling @ file:///tmp/build/80754af9/conda-package-handling_1649105784853/work
cryptography @ file:///tmp/build/80754af9/cryptography_1639414572950/work
debugpy==1.6.0
decorator==5.1.1
entrypoints==0.4
executing==0.8.3
ExifRead==3.0.0
filetype==1.0.13
Flask==2.0.1
idna @ file:///tmp/build/80754af9/idna_1637925883363/work
importlib-metadata==4.11.4
inifile==0.4.1
ipykernel==6.15.0
ipython==8.4.0
itsdangerous==2.1.2

In [25]:
# conda MODULE IS USED FOR TEST

python-import-path 'conda'
linebr
python-import-path-full 'conda'
linebr
python-import-path-all 'conda' | grep 'conda'

matches /home/aveey/miniconda3/lib/python3.9/site-packages/conda/__init__.py
--------------------------------------------------------------------------------
matches /home/aveey/miniconda3/lib/python3.9/site-packages/conda/__init__.py
matches /home/aveey/miniconda3/lib/python3.9/site-packages/conda/common
matches /home/aveey/miniconda3/lib/python3.9/site-packages/conda/common
--------------------------------------------------------------------------------
# /home/aveey/miniconda3/lib/python3.9/encodings/__pycache__/__init__.cpython-39.pyc matches /home/aveey/miniconda3/lib/python3.9/encodings/__init__.py
# code object from '/home/aveey/miniconda3/lib/python3.9/encodings/__pycache__/__init__.cpython-39.pyc'
# /home/aveey/miniconda3/lib/python3.9/__pycache__/codecs.cpython-39.pyc matches /home/aveey/miniconda3/lib/python3.9/codecs.py
# code object from '/home/aveey/miniconda3/lib/python3.9/__pycache__/codecs.cpython-39.pyc'
# /home/aveey/miniconda3/lib/python3.9/encodings/__pycache__/ali

# /home/aveey/miniconda3/lib/python3.9/__pycache__/copyreg.cpython-39.pyc matches /home/aveey/miniconda3/lib/python3.9/copyreg.py
# code object from '/home/aveey/miniconda3/lib/python3.9/__pycache__/copyreg.cpython-39.pyc'
# /home/aveey/miniconda3/lib/python3.9/json/__pycache__/scanner.cpython-39.pyc matches /home/aveey/miniconda3/lib/python3.9/json/scanner.py
# code object from '/home/aveey/miniconda3/lib/python3.9/json/__pycache__/scanner.cpython-39.pyc'
# extension module '_json' loaded from '/home/aveey/miniconda3/lib/python3.9/lib-dynload/_json.cpython-39-x86_64-linux-gnu.so'
# extension module '_json' executed from '/home/aveey/miniconda3/lib/python3.9/lib-dynload/_json.cpython-39-x86_64-linux-gnu.so'
# /home/aveey/miniconda3/lib/python3.9/json/__pycache__/encoder.cpython-39.pyc matches /home/aveey/miniconda3/lib/python3.9/json/encoder.py
# code object from '/home/aveey/miniconda3/lib/python3.9/json/__pycache__/encoder.cpython-39.pyc'
# /home/aveey/miniconda3/lib/python3.9/site-p

In [26]:
# note: gotta hate python!
function python-module-version-full { local module="$1"; python -c "import $module; print([v for v in [getattr($module, a, '') for a in '__VERSION__ VERSION __version__ version'.split()] if v][0])"; }
# TODO: check-error if no value returned
function python-module-version { python-module-version-full "$@" 2> /dev/null; }
function python-package-members() { local package="$1"; python -c "import $package; print(dir($package));"; }
#
alias python-setup-install='log=setup.log;  rename-with-file-date $log;  uname -a > $log;  python setup.py install --record installed-files.list >> $log 2>&1;  ltc $log'
# TODO: add -v (the xargs usage seems to block it)
alias python-uninstall-setup='cat installed-files.list | xargs /bin/rm -vi; rename_files.perl -regex ^ un installed-files.list'


In [27]:
# MODULE USED: mezcla
python-module-version-full mezcla
linebr
python-module-version mezcla
linebr
python-package-members mezcla
linebr

1.3.0
--------------------------------------------------------------------------------
1.3.0
--------------------------------------------------------------------------------
['PYTHON3_PLUS', 'TL', '__VERSION__', '__all__', '__builtins__', '__cached__', '__doc__', '__file__', '__loader__', '__name__', '__package__', '__path__', '__spec__', '__version__', 'debug', 'gh', 'glue_helpers', 'mezcla', 'sys', 'sys_version_info_hack', 'system', 'tpo_common']
--------------------------------------------------------------------------------


In [28]:
## rename-with-file-date REQUIRED
function rename-with-file-date() {
    ## DEBUG: set -o xtrace
    local f new_f
    local move_command="move"
    if [ "$1" = "--copy" ]; then
        ## TODO: move_command="copy"
        move_command="command cp --interactive --verbose --preserve"
        shift
    fi
    for f in "$@"; do
        ## DEBUG: echo "f=$f"
        if [ -e "$f" ]; then
           new_f=$(get-free-filename "$f".$(date --reference="$f" '+%d%b%y') ".")
           ## DEBUG: echo
           eval "$move_command" "$f" "$new_f";
        fi
    done;
    ## DEBUG: set - -o xtrace
}

function get-free-filename() {
    local base="$1"
    local sep="$2"
    local L=1
    local filename="$base"
    ## DEBUG: local -p
    while [ -e "$filename" ]; do
        let L++
        filename="$base$sep$L"
    done;
    ## DEBUG: local -p
    echo "$filename"
}

alias move='mv'
export PAGER=less
export PAGER_CHOPPED="less -S"
export PAGER_NOEXIT="less -+F"
function zless () { zcat "$@" | $PAGER; }
# 
# zhead(file, head-opts)
function zhead () {
    local file="$1"
    shift
    zcat "$file" | head "$@"
}
alias less-='$PAGER_NOEXIT'
alias less-clipped='$PAGER_NOEXIT -S'
alias less-tail='$PAGER_NOEXIT +G'
alias less-tail-clipped='$PAGER_NOEXIT +G -S'
alias ltc=less-tail-clipped


In [29]:
## REQUIRES setup.py (TBC)

#python-setup-install
linebr
#python-uninstall-setup

--------------------------------------------------------------------------------


In [30]:
# ipython(): overrides ipython command to set xterm title
alias set-xterm-window='set_xterm_title.bash'

function ipython() { 
    local ipython=$(which ipython)
    if [ "$ipython" = "" ]; then echo "Error: install ipython first"; return; fi
    set-xterm-window "ipython [$PWD]"
    $ipython "$@"
}

# python-trace(script, arg, ...): Run python SCRIPT with statement tracing
function python-trace {
    local script="$1"
    shift
    $PYTHON -m trace --trace $(which "$script") "$@"
    }


In [31]:
# ipython COMMAND SEEMS TO WORK
ipython -h

/home/aveey/bin/set_xterm_title.bash: line 239: /_set_xterm_title.5195.full.list: Permission denied
/home/aveey/bin/set_xterm_title.bash: line 240: /_set_xterm_title.5195.icon.list: Permission denied
]1;ipython [/tmp/test-py-commands/test-3443]]2;ipython [/tmp/test-py-commands/test-3443]=========
 IPython

Tools for Interactive Computing in Python

    A Python shell with automatic history (input and output), dynamic object
    introspection, easier configuration, command completion, access to the
    system shell and more.  IPython can also be embedded in running programs.

Usage

    ipython [subcommand] [options] [-c cmd | -m mod | file] [--] [arg] ...

    If invoked with no options, it executes the file and exits, passing the
    remaining arguments to the script, just as if you had specified the same
    command with python. You may need to specify `--` before args to be passed
    to the script, to prevent IPython from attempting to parse them. If you
    specify the option 

    Equivalent to: [--TerminalIPythonApp.force_interact=True]
--log-level=<Enum>
    Set the log level by value or name.
    Choices: any of [0, 10, 20, 30, 40, 50, 'DEBUG', 'INFO', 'WARN', 'ERROR', 'CRITICAL']
    Default: 30
    Equivalent to: [--Application.log_level]
--profile-dir=<Unicode>
    Set the profile location directly. This overrides the logic used by the
            `profile` option.
    Default: ''
    Equivalent to: [--ProfileDir.location]
--profile=<Unicode>
    The IPython profile to use.
    Default: 'default'
    Equivalent to: [--BaseIPythonApplication.profile]
--ipython-dir=<Unicode>
    The name of the IPython directory. This directory is used for logging
    configuration (through profiles), history storage, etc. The default is
    usually $HOME/.ipython. This option can also be specified through the
    environment variable IPYTHONDIR.
    Default: ''
    Equivalent to: [--BaseIPythonApplication.ipython_dir]
--config=<Unicode>
    Path to an extra config file 

In [32]:
python-trace l $BIN_DIR/template.py #(need some help to test it properly - seems to function / time consuming)

 --- modulename: template, funcname: <module>
template.py(10): """TODO: what module does (brief)"""
template.py(13): import re
template.py(20): from mezcla import debug
 --- modulename: _bootstrap, funcname: _find_and_load
<frozen importlib._bootstrap>(1004):  --- modulename: _bootstrap, funcname: __init__
<frozen importlib._bootstrap>(153): <frozen importlib._bootstrap>(154):  --- modulename: _bootstrap, funcname: __enter__
<frozen importlib._bootstrap>(157):  --- modulename: _bootstrap, funcname: _get_module_lock
<frozen importlib._bootstrap>(172): <frozen importlib._bootstrap>(173): <frozen importlib._bootstrap>(174): <frozen importlib._bootstrap>(175): <frozen importlib._bootstrap>(176): <frozen importlib._bootstrap>(177): <frozen importlib._bootstrap>(179): <frozen importlib._bootstrap>(180): <frozen importlib._bootstrap>(183):  --- modulename: _bootstrap, funcname: __init__
<frozen importlib._bootstrap>(59): <frozen importlib._bootstrap>(60): <frozen importlib._bootstrap>(61): <f

<frozen importlib._bootstrap_external>(142): <frozen importlib._bootstrap_external>(1525): <frozen importlib._bootstrap_external>(1526):  --- modulename: _bootstrap_external, funcname: _fill_cache
<frozen importlib._bootstrap_external>(1567): <frozen importlib._bootstrap_external>(1568): <frozen importlib._bootstrap_external>(1569): <frozen importlib._bootstrap_external>(1576): <frozen importlib._bootstrap_external>(1577): <frozen importlib._bootstrap_external>(1593): <frozen importlib._bootstrap_external>(1527): <frozen importlib._bootstrap_external>(1529):  --- modulename: _bootstrap_external, funcname: _relax_case
<frozen importlib._bootstrap_external>(70): <frozen importlib._bootstrap_external>(1533): <frozen importlib._bootstrap_external>(1534): <frozen importlib._bootstrap_external>(1536): <frozen importlib._bootstrap_external>(1548): <frozen importlib._bootstrap_external>(1549): <frozen importlib._bootstrap_external>(1550):  --- modulename: _bootstrap_external, funcname: _path_j

<frozen importlib._bootstrap>(233): <frozen importlib._bootstrap_external>(1554): <frozen importlib._bootstrap_external>(1548): <frozen importlib._bootstrap_external>(1549): <frozen importlib._bootstrap_external>(1550):  --- modulename: _bootstrap_external, funcname: _path_join
<frozen importlib._bootstrap_external>(123): <frozen importlib._bootstrap_external>(124): <frozen importlib._bootstrap_external>(123):  --- modulename: _bootstrap_external, funcname: <listcomp>
<frozen importlib._bootstrap_external>(123): <frozen importlib._bootstrap_external>(124): <frozen importlib._bootstrap_external>(123): <frozen importlib._bootstrap_external>(123): <frozen importlib._bootstrap_external>(124): <frozen importlib._bootstrap_external>(123): <frozen importlib._bootstrap_external>(123): <frozen importlib._bootstrap_external>(1553):  --- modulename: _bootstrap, funcname: _verbose_message
<frozen importlib._bootstrap>(233): <frozen importlib._bootstrap_external>(1554): <frozen importlib._bootstrap

<frozen importlib._bootstrap_external>(123): <frozen importlib._bootstrap_external>(124): <frozen importlib._bootstrap_external>(123):  --- modulename: _bootstrap_external, funcname: <listcomp>
<frozen importlib._bootstrap_external>(123): <frozen importlib._bootstrap_external>(124): <frozen importlib._bootstrap_external>(123): <frozen importlib._bootstrap_external>(123): <frozen importlib._bootstrap_external>(124): <frozen importlib._bootstrap_external>(123): <frozen importlib._bootstrap_external>(123): <frozen importlib._bootstrap_external>(1553):  --- modulename: _bootstrap, funcname: _verbose_message
<frozen importlib._bootstrap>(233): <frozen importlib._bootstrap_external>(1554): <frozen importlib._bootstrap_external>(1548): <frozen importlib._bootstrap_external>(1558): <frozen importlib._bootstrap_external>(1563): <frozen importlib._bootstrap_external>(1398): <frozen importlib._bootstrap_external>(1399): <frozen importlib._bootstrap_external>(1389): <frozen importlib._bootstrap_ex

<frozen importlib._bootstrap_external>(70): <frozen importlib._bootstrap_external>(1533): <frozen importlib._bootstrap_external>(1534): <frozen importlib._bootstrap_external>(1536): <frozen importlib._bootstrap_external>(1548): <frozen importlib._bootstrap_external>(1549): <frozen importlib._bootstrap_external>(1550):  --- modulename: _bootstrap_external, funcname: _path_join
<frozen importlib._bootstrap_external>(123): <frozen importlib._bootstrap_external>(124): <frozen importlib._bootstrap_external>(123):  --- modulename: _bootstrap_external, funcname: <listcomp>
<frozen importlib._bootstrap_external>(123): <frozen importlib._bootstrap_external>(124): <frozen importlib._bootstrap_external>(123): <frozen importlib._bootstrap_external>(123): <frozen importlib._bootstrap_external>(124): <frozen importlib._bootstrap_external>(123): <frozen importlib._bootstrap_external>(123): <frozen importlib._bootstrap_external>(1553):  --- modulename: _bootstrap, funcname: _verbose_message
<frozen im

...

 --- modulename: sre_parse, funcname: __next
sre_parse.py(234):         index = self.index
sre_parse.py(235):         try:
sre_parse.py(236):             char = self.decoded_string[index]
sre_parse.py(240):         if char == "\\":
sre_parse.py(247):         self.index = index + 1
sre_parse.py(248):         self.next = char
sre_parse.py(257):         return this
sre_parse.py(548):                 if this is None:
sre_parse.py(551):                 if this == "]" and set:
sre_parse.py(553):                 elif this[0] == "\\":
sre_parse.py(554):                     code1 = _class_escape(source, this)
 --- modulename: sre_parse, funcname: _class_escape
sre_parse.py(297):     code = ESCAPES.get(escape)
sre_parse.py(298):     if code:
sre_parse.py(300):     code = CATEGORIES.get(escape)
sre_parse.py(301):     if code and code[0] is IN:
sre_parse.py(303):     try:
sre_parse.py(304):         c = escape[1:2]
sre_parse.py(305):         if c == "x":
sre_parse.py(311):         elif c == "u" and

sre_parse.py(180):             if op is BRANCH:
sre_parse.py(189):             elif op is CALL:
sre_parse.py(193):             elif op is SUBPATTERN:
sre_parse.py(197):             elif op in _REPEATCODES:
sre_parse.py(201):             elif op in _UNITCODES:
sre_parse.py(202):                 lo = lo + 1
sre_parse.py(203):                 hi = hi + 1
sre_parse.py(179):         for op, av in self.data:
sre_parse.py(220):         self.width = min(lo, MAXREPEAT - 1), min(hi, MAXREPEAT)
sre_parse.py(221):         return self.width
sre_compile.py(541):     if hi > MAXCODE:
sre_compile.py(543):     if lo == 0:
sre_compile.py(547):     prefix = []
sre_compile.py(548):     prefix_skip = 0
sre_compile.py(549):     charset = [] # not used
sre_compile.py(550):     if not (flags & SRE_FLAG_IGNORECASE and flags & SRE_FLAG_LOCALE):
sre_compile.py(552):         prefix, prefix_skip, got_all = _get_literal_prefix(pattern, flags)
 --- modulename: sre_compile, funcname: _get_literal_prefix
sre_compile.p

sre_compile.py(343):         q = charmap.find(0, p)
sre_compile.py(344):         if q < 0:
sre_compile.py(347):         runs.append((p, q))
sre_compile.py(337):         p = charmap.find(1, q)
sre_compile.py(338):         if p < 0:
sre_compile.py(339):             break
sre_compile.py(348):     if runs is not None:
sre_compile.py(350):         for p, q in runs:
sre_compile.py(351):             if q - p == 1:
sre_compile.py(352):                 out.append((LITERAL, p))
sre_compile.py(350):         for p, q in runs:
sre_compile.py(351):             if q - p == 1:
sre_compile.py(352):                 out.append((LITERAL, p))
sre_compile.py(350):         for p, q in runs:
sre_compile.py(355):         out += tail
sre_compile.py(357):         if hascased or len(out) < len(charset):
sre_compile.py(360):         return charset, hascased
sre_compile.py(121):             if flags & SRE_FLAG_IGNORECASE and flags & SRE_FLAG_LOCALE:
sre_compile.py(123):             elif not hascased:
sre_compile.py

sre_compile.py(780):     return _sre.compile(
sre_compile.py(781):         pattern, flags | p.state.flags, code,
sre_compile.py(782):         p.state.groups-1,
 --- modulename: sre_parse, funcname: groups
sre_parse.py(83):         return len(self.groupwidths)
sre_compile.py(783):         groupindex, tuple(indexgroup)
sre_compile.py(780):     return _sre.compile(
re.py(305):     if not (flags & DEBUG):
 --- modulename: enum, funcname: __and__
enum.py(978):         if not isinstance(other, (self.__class__, int)):
enum.py(980):         return self.__class__(self._value_ & self.__class__(other)._value_)
 --- modulename: enum, funcname: __call__
enum.py(383):         if names is None:  # simple value lookup
enum.py(384):             return cls.__new__(cls, value)
 --- modulename: enum, funcname: __new__
enum.py(674):         if type(value) is cls:
enum.py(679):         try:
enum.py(680):             return cls._value2member_map_[value]
 --- modulename: enum, funcname: __call__
enum.py(383):

sre_parse.py(250):         if char == self.next:
sre_parse.py(253):         return False
sre_parse.py(829):             if group is not None:
sre_parse.py(830):                 try:
sre_parse.py(831):                     group = state.opengroup(name)
 --- modulename: sre_parse, funcname: opengroup
sre_parse.py(85):         gid = self.groups
 --- modulename: sre_parse, funcname: groups
sre_parse.py(83):         return len(self.groupwidths)
sre_parse.py(86):         self.groupwidths.append(None)
sre_parse.py(87):         if self.groups > MAXGROUPS:
 --- modulename: sre_parse, funcname: groups
sre_parse.py(83):         return len(self.groupwidths)
sre_parse.py(89):         if name is not None:
sre_parse.py(95):         return gid
sre_parse.py(834):             sub_verbose = ((verbose or (add_flags & SRE_FLAG_VERBOSE)) and
sre_parse.py(834):             sub_verbose = ((verbose or (add_flags & SRE_FLAG_VERBOSE)) and
sre_parse.py(836):             p = _parse_sub(source, state, sub_verbose, n

In [33]:
# which-python SHOWS THE PATH OF PYTHON
alias which-python='which python'
which-python
linebr
alias which-py3='which python3' #(ADDED FOR PYTHON3)
which-py3

In [34]:
# py-diff : CHECKS THE DIFFERENCE BETWEEN THE PYTHON FILES
# TODO: specify options before the pattern (or modify do_diff.sh to allow after)
function py-diff () { do_diff.sh '*.py *.mako' "$@" 2>&1 | $PAGER; }
pwd

In [35]:
#py-diff $BIN_DIR/tests/batspp.py $BIN_DIR/tests/ipynb_to_batspp.py
rm -rf ./*
printf "print('THIS IS A TEST')" > abc.py
printf "print('THIS IS A TEST')" > xyz.py
printf "print('THIS IS A TEST11')" > abc1.py
ls

abc1.py  abc.py  xyz.py


In [36]:
# $ py-diff ./ 
#(help required - process not ending)

In [37]:
# TEST NOT APPLICABLE RN 
function kivy-win32-env {
   export PYTHONPATH='c:/cartera-de-tomas/python;c:/Program-Misc/python/kivy-1-9-0/kivy27'
   kivy_dir="/c/Program-Misc/python/kivy-1-9-0"
   python_dir="$kivy_dir/Python27"
   prepend-path "$kivy_dir:$kivy_dir/Python27:$kivy_dir/tools:$kivy_dir/Python27/Scripts:$kivy_dir/gstreamer/bin:$kivy_dir/MinGW/bin:$kivy_dir/SDL2/bin"
}

In [38]:
alias elide-data='python -m transpose_data --elide'
alias kill-python="kill_em.sh --filter 'ipython|emacs' python"
alias kill-python-all="kill_em.sh python"

In [57]:
# # ERRORS = OSTYPE is 'undefined variable' 
# # NOTE: elide-data shows RuntimeError if any testfile is named abc.py

# $ echo $OSTYPE
#   linebr
#   elide-data $BIN_DIR/template.py
#   linebr
#   kill-python
#   linebr
#   kill-python-all

# | linux-gnu
# | --------------------------------------------------------------------------------
# | /home/aveey/miniconda3/bin/python: No module named transpose_data
# | --------------------------------------------------------------------------------
# | pattern=/:[0-9][0-9] [^ ]*python/
# | filter=/ipython|emacs/
# | OSTYPE: Undefined variable.
# | --------------------------------------------------------------------------------
# | pattern=/:[0-9][0-9] [^ ]*python/
# | filter=/($)(^)/
# | OSTYPE: Undefined variable.

echo $OSTYPE
linebr
elide-data $BIN_DIR/template.py


linux-gnu
--------------------------------------------------------------------------------
/home/aveey/miniconda3/bin/python: No module named transpose_data


: 1

In [44]:
# run-jupyter-notebook(port=18888): run jupyter notebook on PORT
alias TODAY='date'
alias extract-matches='extract_matches.perl'

function run-jupyter-notebook () {
    local port="$1"; if [ "$port" = "" ]; then port=8888; fi
    local ip="$2"; if [ "$ip" = "" ]; then ip="127.0.0.1"; fi
    local log="$TEMP/jupyter-$(TODAY).log"
    jupyter notebook --NotebookApp.token='' --no-browser --port $port --ip $ip >> "$log" 2>&1 &
    echo "$log"
    # Let jupyter initialize
    local delay=5
    echo "sleeping $delay seconds for log to stabalize (effing jupyter)"
    sleep $delay
    # TODO: resolve problem extracting URL
    # TEMP:
    tail "$log"
    # Show URL
    echo -n "URL: "
    extract-matches 'http:\S+' "$log" | sort -u
}
alias jupyter-notebook-redir=run-jupyter-notebook
alias jupyter-notebook-redir-open='run-jupyter-notebook 8888 0.0.0.0'

In [46]:
# # ERROR GENERATED (see below)
# $ jupyter-notebook-redir-open

# | [1] 5335
# | /jupyter-Sun Aug 28 08:13:40 AM +0545 2022.log
# | sleeping 5 seconds for log to stabalize (effing jupyter)
# | bash: /jupyter-Sun Aug 28 08:13:40 AM +0545 2022.log: Permission denied
# | [1]+  Exit 1                  jupyter notebook --NotebookApp.token='' --no-browser --port $port --ip $ip >> "$log" 2>&1
# | tail: cannot open '/jupyter-Sun Aug 28 08:13:40 AM +0545 2022.log' for reading: No such file or directory
# | URL: Can't open /jupyter-Sun Aug 28 08:13:40 AM +0545 2022.log: No such file or directory at /home/aveey/bin/extract_matches.perl line 132.


In [47]:
# Python-based utilities
function extract-text() { python -m extract_document_text "$@"; }
alias xtract-text='extract-text'


In [54]:
# # ERROR - MODULE NOT FOUND

# $ rm -rf ./*
#   printf "print('THIS IS A TEST FOR TEXT EXTRACT ALIAS.')" > textex.py
#   xtract-text ./textex.py

# | /home/aveey/miniconda3/bin/python: No module named extract_document_text

/home/aveey/miniconda3/bin/python: No module named extract_document_text


: 1

In [58]:
function test-script () {
    local base=$(basename "$1" .py)
    local date=$(todays-date)
    # note: uses both Mercurial root and . (in case not in repository)
    local root=$(hg root)
    PYTHONPATH="$root:.:$SANDBOX/tests:$PYTHONPATH" $NICE $PYTHON tests/test_$base.py --verbose >| tests/_test_$base.$date.log 2>&1;
    less-tail tests/_test_$base.$date.log;
}
#
alias test-script-debug='ALLOW_SUBCOMMAND_TRACING=1 DEBUG_LEVEL=5 MISC_TRACING_LEVEL=5 test-script'


In [59]:
test-script ./textex.py

bash: hg: command not found
bash: tests/_test_textex.28aug22.log: No such file or directory
tests/_test_textex.28aug22.log: No such file or directory


: 1

In [60]:
# randomize-datafie(file, [num[): randomize datafile optionally pruned to NUM lines, preserving header line
#
function randomize-datafile() {
    local file="$1"
    local num_lines="$2"
    if [ "$num_lines" = "" ]; then num_lines=$(wc -l "$file"); fi
    #
    head -1 "$file"
    tail --lines=+2 "$file" | python -m randomize_lines | head -$num_lines
}


In [61]:
# ERROR : MISSING MODULE (No module named randomize_lines)
randomize-datafile $BIN_DIR/tests/ipynb_to_batspp.py


#! /usr/bin/env python
#! /usr/bin/env python

import sys
import os

filename_arg = sys.argv
file_in_ipynb = filename_arg[1]

def batspp_rename():
    file_in_batspp = file_in_ipynb.replace(".ipynb", ".batspp")#<--CONVERTS EXTENSION TO BATSPP
    RENAME_COMMAND = f"mv {file_in_ipynb} {file_in_batspp}"#<--COMMAND TO BE EXECUTED
    
    os.system(RENAME_COMMAND)
    print(f"Changes were made to {file_in_ipynb}.\n\nFILE RENAMED:\n{file_in_ipynb} --> {file_in_batspp}")

# START OF MAIN #
if ".ipynb" in file_in_ipynb:
    batspp_rename()
else:
    print (f"The selected file is not an IPython file.\nNo changes were made to the file: {file_in_ipynb}")    
/home/aveey/miniconda3/bin/python: No module named randomize_lines


In [62]:
# filter-random(pct, file, [include_header=1])Randomize lines based on percentages, using output lile (e.g., _r10pct-fubar.data).
# Notes:
# - By default, includes first line assuming it is header line.
# - Includes support for compressed files (both input and output).
function filter-random() {
    local pct="$1"
    local file="$2"
    local include_header="$3"
    if [ "$include_header" == "" ]; then include_header=1; fi

    # Derive settings from input arguments
    local ratio=$(perl -e "printf('%.3f', ($pct / 100.0));")
    local compressed=0
    if [[ $file =~ .gz ]]; then compressed=1; fi
    local dir=$(dirname $file)
    local base=$(basename $file)
    local type="cat"
    local result="$dir/_r${pct}pct-$base"

    # Filter the file, optionally uncompressing
    if [ "$compressed" = "1" ]; then 
       type="zcat"; 
       result=$(echo "$result" | perl -pe 's/.gz$//;')
    fi
    local opts=""
    if [ "$include_header" = "1" ]; then opts="$opt --include-header"; fi
    $type "$file" | $PYTHON -m filter_random $opts --ratio $ratio - > "$result" 2> "$result.log"

    # Compress result if original compressed
    if [ "$compressed" = "1" ]; then 
       gzip --force "$result"; 
    fi
}

In [82]:
# filter-random _r10pct-fubar.data (TBF - NEED HELP OPERATING)

syntax error at -e line 1, near "(."
Execution of -e aborted due to compilation errors.
dirname: missing operand
Try 'dirname --help' for more information.
basename: missing operand
Try 'basename --help' for more information.
bash: /_r./www.google.compct-: No such file or directory
cat: '': No such file or directory


In [70]:
# Load supporting scripts
#
function conditional-source () { if [ -e "$1" ]; then source "$1"; else echo "Warning: bash script file not found (so not sourced):"; echo "    $1"; fi; }
function quiet-unalias {
    ## HACK: do nothing if running under bats-core
    if [ "$BATS_TEST_FILENAME" != "" ]; then
        if [ "$BATCH_MODE" != "1" ]; then
            echo "Ignoring unalias over $* for sake of bats"
        fi
        return
    fi
    ## OLD: unalias "$@" 2> /dev/null;
    unalias "$@" 2> /dev/null || true;
    ## OLD: echo > /dev/null;
}

conditional-source $BIN_DIR/anaconda-aliases.bash
conditional-source $BIN_DIR/git-aliases.bash



In [71]:
function curl-dump () {
    local url="$1";
    local base=$(basename $url);
    curl $url > $base;
}
# EX: url-path $BIN/templata.html => "file:///$BIN/template.html"
function url-path () {
    local file="$1"
    echo $(realpath "$file") | perl -pe 's@^@file:///@;'
}

In [77]:
# TESTS FOR curl-dump AND url-path
curl-dump https://www.google.com/
linebr
ls -l
linebr
url-path $BIN_DIR/tests/batspp.py

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 16484    0 16484    0     0  40812      0 --:--:-- --:--:-- --:--:-- 40903
--------------------------------------------------------------------------------
total 24
-rw-rw-r-- 1 aveey aveey    47 Aug 28 08:19 textex.py
-rw-rw-r-- 1 aveey aveey 16484 Aug 28 08:43 www.google.com
--------------------------------------------------------------------------------
file:////home/aveey/tom-project/shell-scripts/tests/batspp.py


In [79]:
function invoke-browser() {
    local browser_executable="$1"
    local file="$2"
    if [ "$file" != "" ]; then
        if [[ ! $file =~ http ]]; then
            file=$(url-path "$file")
        fi
    fi
    ## TODO?
    ## if [ ! -e "$browser_executable" ]; then
    ##     browser_executable_path=$(which "browser_executable")
    ##     if [ "$browser_executable_path" = "" ]; then browser_executable="$_path"; fi   
    ## fi
    local browser_base=$(basename "$browser_executable")
    $browser_executable "$file" >> $TEMP/$browser_base.$(TODAY).log 2>&1 &
}

alias firefox='invoke-browser "'"$(which firefox)"'"'

In [80]:
firefox (#TESTS REMAINS FOR invoke-browser)

[1] 6452


: 1